# Exploring Car Sales Data

## The purpose of this work is to ensure sales data remains relevant and no outliers shall distort our data we will use to determine the following:
## The average cost per type of vehicle, cost per odometer, cost per fuel type, how long vehicles remain on the lot and the average cost of a vehicle on the lot.

In [28]:
import plotly.express as px
import streamlit as st
import pandas as pd

load datasets

In [29]:
vehicles = pd.read_csv('/Users/user/Downloads/sprint4/vehicles_us.csv')
print(vehicles.head(1))
vehicles.info()

   price  model_year   model condition  cylinders fuel  odometer transmission  \
0   9400      2011.0  bmw x5      good        6.0  gas  145000.0    automatic   

  type paint_color  is_4wd date_posted  days_listed  
0  SUV         NaN     1.0  2018-06-23           19  
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed  

In [ ]:
vehicles['model_year'] = vehicles['model_year'].fillna( 
    vehicles.groupby('model')['model_year'].transform('median')
)
vehicles['odometer'] = vehicles['odometer'].fillna(
    vehicles.groupby('model')['odometer'].transform('median')
)
vehicles['cylinders'] = vehicles['cylinders'].fillna(
    vehicles.groupby('model')['cylinders'].transform(lambda x: x.mode()[0] if not x.mode().empty else None)
)


clean dataset

In [ ]:
vehicles['is_4wd'] = vehicles['is_4wd'].fillna(0).astype(int)
vehicles['paint_color'] = vehicles['paint_color'].fillna('Unknown')
vehicles = vehicles[vehicles['price'] <= 100000]
vehicles = vehicles[vehicles['price'] >= 100]
vehicles = vehicles[vehicles['odometer'] <= 500000]
vehicles = vehicles[vehicles['model_year'] >= 1955]

##group data

Assumption: The `model_year` is associated with the vehicle model.
Approach: Use the median `model_year` for the same `model` to fill missing values. This tactful approach leverages the relationship between `model` and `model_year`.

Assumption: Mileage (odometer) can vary by model.
Approach: Use the median odometer value for vehicles of the same model to fill missing values. This ensures that imputed values are realistic for the respective vehicle type.

ssumption: `cylinders` is often consistent for a given model.
Approach: Use the mode (most frequently occurring value) of `cylinders` for the same `model` to restore missing values.


depict sales data

In [32]:


# Scatter plot for Price vs. Model Year with Color by Condition
fig = px.scatter(
    vehicles,
    x='model_year',
    y='price',
    color='condition',  # Color by condition
     color_discrete_sequence=px.colors.qualitative.Set1,  # Explicit color palette
    title='Price vs. Model Year',
    labels={'model_year': 'Model Year', 'price': 'Price'}
)

# Show the plot
fig.show()



The graph above shows that new condition vehciles sell for the most value within the first 2 years.
It also depicts how a vehicles depreciation stops approximately around 20 years old and classics gain value after 50 years given the proper condition.

In [33]:
# Histogram for Price Distribution
fig = px.histogram(
vehicles,
x='price',
nbins=100,
title='Price Distribution',
labels={'price': 'Vehicle Price'},
color_discrete_sequence=['blue']
)


fig.show()


This dealerships sales data shows they mainly stock vehicles with value between $3000 and $10000

In [34]:
# Scatter plot for Price vs. Odometer
fig = px.scatter(
    vehicles,
    x='odometer',
    y='price',
    color='fuel',
     color_discrete_sequence=px.colors.qualitative.Set1,  # Explicit color palette
    title='Price vs. Odometer',
    labels={'odometer': 'Odometer (miles)', 'price': 'Price'}
)
fig.show()


Diesels retain their value the most dispite the miles being put on them

In [35]:
# Histogram for Condition Distribution
fig = px.histogram(
    vehicles,
    x='condition',
    title='Condition Distribution',
    labels={'condition': 'Car Condition'},
    color_discrete_sequence=['green']
)
fig.show()


This dealership mainly sells vehicles in excellent to good condition

In [36]:
# Group by 'condition' and calculate the average price
average_price_by_condition = vehicles.groupby('condition')['price'].mean().reset_index()

# Rename columns for better readability
average_price_by_condition.columns = ['Condition', 'Average Price']

# Create a bar chart to show the average price
fig = px.bar(
    average_price_by_condition,
    x='Condition',
    y='Average Price',
    title='Average Price by Vehicle Condition',
    text='Average Price',  # Display the average price as text on the bars
    labels={'Condition': 'Vehicle Condition', 'Average Price': 'Average Price ($)'},
    color='Condition',
    color_discrete_sequence=px.colors.qualitative.Set1,  # Explicit color palette
)

# Format the text on bars and show the chart
fig.update_traces(texttemplate='$%{text:.2f}', textposition='outside')
fig.update_layout(yaxis_title='Average Sale Price ($)')
fig.show()


The illustration above shows that new vehicles are twice as costly as excellent conditioned vehicles. buying used but excellent condition is a no brainer

In [37]:
# Create a new column for odometer bins, grouped by 10,000
vehicles['odometer_bin'] = pd.cut(vehicles['odometer'], bins=range(0, int(vehicles['odometer'].max()) + 10000, 10000))

# Group by odometer bins and calculate the average price for each bin
average_price_by_odometer = vehicles.groupby('odometer_bin')['price'].mean().reset_index()

# Convert the bins to string format for better readability in the plot
average_price_by_odometer['odometer_bin'] = average_price_by_odometer['odometer_bin'].astype(str)

# Create a bar chart to show average sale price by odometer range
fig = px.bar(
    average_price_by_odometer,
    x='odometer_bin',
    y='price',
    title='Average Sale Price by Odometer Range',
    labels={'odometer_bin': 'Odometer Range (miles)', 'price': 'Average Price ($)'},
    text='price',
    
)

# Format the text on bars and display the chart
fig.update_traces(texttemplate='$%{text:.2f}', textposition='outside')
fig.update_layout(
    xaxis_title='Odometer Range (miles)',
    yaxis_title='Average Price ($)',
    xaxis_tickangle=45  # Rotate the x-axis labels for readability
)
fig.show()


the graph above shows that vehicle depreciation stabilizes after 150k miles

In [38]:
# Histogram for Days Listed Distribution
fig = px.histogram(
    vehicles,
    x='days_listed',
    nbins=30,
    title='Days Listed Distribution',
    labels={'days_listed': 'Days Listed'},
    color_discrete_sequence=['orange']
)
fig.show()


On average, vehicles are sold within 1 month

In [39]:
# Box plot for Price by Car Type
fig = px.box(
    vehicles,
    x='type',
    y='price',
    title='Price by Vehicle Type',
    labels={'type': 'Vehicle Type', 'price': 'Price'},
    color='type', color_discrete_sequence=px.colors.qualitative.Set1,  # Explicit color palette

    
)
fig.show()


This dynamic illustration show just how much more those big vehicle cost vs a practical consumer car